In [2]:
from __future__ import print_function
from Bio.PDB import *
import os
import numpy as np
import collections
import pandas as pd
from scipy.spatial import distance
from pygsp import graphs, features
import networkx as nx
import matplotlib.pyplot as plt
import subprocess
from pygsp import utils
from pygsp import graphs, filters
from sklearn.linear_model import LinearRegression

In [3]:
signals_and_cutoffs = {'molecular_weight': 0.42, 
                       'hydrophobicity': 0.42, 
                       'node_degree': 0.42, 
                       'node_weighted_degree': 0.42, 
                       'residue_count': 0.42, 
                       'clustering_coeff': 0.42,
                      'conservation_score': 0.42}

signals_wavelet = ['molecular_weight_1','molecular_weight_2','molecular_weight_3','molecular_weight_4', 'hydrophobicity_1','hydrophobicity_2','hydrophobicity_3','hydrophobicity_4','node_degree_1','node_degree_2','node_degree_3','node_degree_4', 'node_weighted_degree_1', 'node_weighted_degree_2','node_weighted_degree_3' , 'node_weighted_degree_4','residue_count_1','residue_count_2','residue_count_3','residue_count_4' ,'clustering_coeff_1','clustering_coeff_2','clustering_coeff_3','clustering_coeff_4','conservation_score_1','conservation_score_2','conservation_score_3','conservation_score_4']
signals = ['molecular_weight', 'hydrophobicity', 'node_degree', 'node_weighted_degree', 'residue_count', 'clustering_coeff','conservation_score']

In [4]:
amino_lookup = {'CYS': 'C', 'ASP': 'D', 'SER': 'S', 'GLN': 'Q', 'LYS': 'K',
     'ILE': 'I', 'PRO': 'P', 'THR': 'T', 'PHE': 'F', 'ASN': 'N',
     'GLY': 'G', 'HIS': 'H', 'LEU': 'L', 'ARG': 'R', 'TRP': 'W',
     'ALA': 'A', 'VAL':'V', 'GLU': 'E', 'TYR': 'Y', 'MET': 'M','CCS':'C','AC5':'L'}
amino_molecular_mass = {'A': 89.09404, 'R': 174.20274, 'N': 132.11904, 'D': 133.10384, 'C': 121.15404,
                        'Q': 146.14594, 'E': 147.13074, 'G': 75.06714, 'H': 155.15634, 'I': 131.17464,
                        'L': 131.17464, 'K': 146.18934, 'M': 149.20784, 'F': 165.19184, 'P': 115.13194,
                        'S': 105.09344, 'T': 119.12034, 'W': 204.22844, 'Y': 181.19124, 'V': 117.14784}
amino_hydrophobicity = {'A': 1.8, 'R': -4.5, 'N': -3.5, 'D': -3.5, 'C': 2.5,
                        'Q': -3.5, 'E': -3.5, 'G': -0.4, 'H': -3.2, 'I': 4.5,
                        'L': 3.8, 'K': -3.9, 'M': 1.9, 'F': 2.8, 'P': -1.6,
                        'S': -0.8, 'T': -0.7, 'W': -0.9, 'Y': -1.3, 'V': 4.2}

In [5]:
def crawl_pdb(path):
    '''This function reads pdb files and stores their distance matrix and sequence'''
    parser = PDBParser()
    pdb_files = sorted(os.listdir(path))
    pdbinfo_dict = dict()
    for pdb in pdb_files:
        info = dict()
        info[id] = pdb
        structure = parser.get_structure('pdb_file', path  + pdb )
        coordinates = []
        labels = list()
        for model in structure:
            for chain in model:
                for residue in chain:
                    try:
                        if residue.get_resname() in amino_lookup:
                            coordinates.append(residue['CA'].get_coord())
                            labels.append(residue.get_resname())
                    except KeyError:
                        pass
                break  ## working on chain id A only
            break      ## Working on model id 0 only
        coords = np.asmatrix(coordinates)
        distance_matrix = distance.squareform(distance.pdist(coords))
        info['coords'] = coords
        info['distance_matrix'] = distance_matrix
#         print(np.unique(labels))
        info['sequence'] = ''.join([amino_lookup[s] for s in labels if s in amino_lookup])
        pdbinfo_dict[pdb] = info
    return pdbinfo_dict
 
def get_graph(distance_matrix, network_type, rig_cutoff=8, lin_cutoff=12):
    distance_matrix[distance_matrix >= rig_cutoff] = 0
    if network_type == 'rig-boolean':
        distance_matrix[distance_matrix > 0] = 1
    elif network_type == 'weighted-rig':
        for i in range(np.shape(distance_matrix)[0]):
            for j in range(np.shape(distance_matrix)[1]):
                if distance_matrix[i, j] > 0:
                    distance_matrix[i, j] = abs(j - i)
    elif network_type == 'weighted-lin':
        for i in range(np.shape(distance_matrix)[0]):
            for j in range(np.shape(distance_matrix)[1]):
                if distance_matrix[i, j] > 0:
                    if abs(i - j) >= lin_cutoff or abs(i - j) == 1:
                        distance_matrix[i, j] = abs(i - j)
                    else:
                        distance_matrix[i, j] = 0
    elif network_type == 'lin':
        for i in range(np.shape(distance_matrix)[0]):
            for j in range(np.shape(distance_matrix)[1]):
                if distance_matrix[i, j] > 0:
                    if abs(i - j) >= lin_cutoff or abs(i - j) == 1:
                        distance_matrix[i, j] = 1
                    else:
                        distance_matrix[i, j] = 0
    else:
        print('Invalid Choice! ' + network_type)
        return None
    G = graphs.Graph(distance_matrix, lap_type='normalized')
    G.compute_fourier_basis()
    return G
 
def get_signal(G, seq, pdb, signal):
    if signal == 'molecular_weight':
        s = np.asarray([amino_molecular_mass[aa] for aa in seq])
    elif signal == 'hydrophobicity':
        s = np.asarray([amino_hydrophobicity[aa] for aa in seq])
    elif signal == 'node_degree':
        s = G.d
    elif signal == 'node_weighted_degree':
        adj = G.W.todense()
        s = np.ravel(adj.sum(axis=0)) / 2
    elif signal == 'avg_adj_degree':
        s = features.compute_avg_adj_deg(G)
        s = np.ravel(s)
    elif signal == 'clustering_coeff':
        N = nx.from_scipy_sparse_matrix(G.W)
        s = nx.clustering(N)
        s = np.asarray(list(s.values()))
    elif signal == 'aaalpha_helix':
        s = eng.aaalpha_helixfasman(seq)
        s = np.array(s._data)
    elif signal == 'residue_count':
        residue_counts = collections.Counter(seq)
        s = np.asarray([residue_counts[s] for s in seq])
    elif signal == 'conservation_score':
        #https://compbio.cs.princeton.edu/conservation/
        filename = pdb.split('.')[0]
#         cmd = ['python3 ./pdb2fasta-master/pdb2fasta.py '+pdb_path+''+pdb+' > ./pdb2fasta-master/'+filename+'.fasta']
#         print(cmd)
#         process = subprocess.call(cmd, shell=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        with open('./pdb2fasta-master/'+filename+'.fasta', 'w') as the_file:
            the_file.write('>'+filename+':A\n'+seq+"-")
        process = 0
        if process ==0:
            s = []
            cmd = ['python2 ./pdb2fasta-master/conservation_code/score_conservation.py -alignfile ./pdb2fasta-master/'+filename+'.fasta > ./pdb2fasta-master/'+filename+'.csv']
#             print(cmd)
            process = subprocess.call(cmd, shell=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
            if process ==0:
                with open('./pdb2fasta-master/'+filename+'.csv') as f:
                    for i in range(5):
                        next(f)
                    for line in f:
#                         print(line.split("\t")[1])
                        s.append(float(line.split("\t")[1]))
        s = np.array(s)
    else:
        print ('Invalid Choice! ' + signal)
    return s
 
def get_filtered_signal(G, signal, cutoff,type_spatial):
    if type_spatial == 'fourier':
        gftsignal = G.gft(signal)
        signal_hat = gftsignal
        value = np.sum(abs(signal_hat[G.e < G.lmax*cutoff])) / np.sum(abs(signal_hat))
        return value
    elif type_spatial == 'wavelet':
        N_f=4
        scales = utils.compute_log_scales(1, len(signal), N_f-1)
        mex = filters.Abspline(G, Nf=N_f,scales=scales)
#         for i, signal in enumerate(exp):
        signal_filtered_hat = mex.filter(signal)
        signal_filtered_hat = np.abs(signal_filtered_hat)
        for j in range(signal_filtered_hat.shape[1]):
                p = np.percentile(signal_filtered_hat[:,j], 70) 
                signal_filtered_hat[np.where(signal_filtered_hat[:,j]<p),j] = 0
#         inv_fil = mex.filter(signal_filtered_hat)
#         print(inv_fil.shape)
        signal_filtered_hat = np.mean(np.abs(signal_filtered_hat),axis=0)
        return signal_filtered_hat

In [ ]:
path = './pdb_files/ant_real/'
pdbinfo_dict = crawl_pdb(path)
lfc_cutoff = 0.42
model = 'weighted-rig'
# print (lfc_cutoff, end=' : ')
gsp_features = pd.DataFrame(columns=signals_wavelet+['class'])
 
path_files = './pdb_files/ant_real/'
for pdb in pdbinfo_dict.keys():
    row = []
    c=0
    G = get_graph(pdbinfo_dict[pdb]['distance_matrix'], network_type=model, rig_cutoff=7.3)
    for signal_name in signals:
        signal = get_signal(G, pdbinfo_dict[pdb]['sequence'],pdb,signal=signal_name)
        value = get_filtered_signal(G,signal,lfc_cutoff,type_spatial='wavelet')       
        row.extend(value)
    row.append(c)
    gsp_features.loc[pdb] = row

In [7]:
path = './pdb_files/ant_real/'

In [8]:
pdbinfo_dict = crawl_pdb(path)

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4092.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4126.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4160.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4211.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4344.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 5121.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 5162.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 5203.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 5442.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 5062.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 13462.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 13487.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 13512.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 13537.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain E is discontinuous at line 13562.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/Structu

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4503.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 4522.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4539.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 4775.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 8804.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 12529.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 25061.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 25088.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 25115.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 25142.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/Structu

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4082.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4167.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4251.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4365.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 3445.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4916.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4921.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4942.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 5061.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 8336.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 7888.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 7946.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 8003.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 8060.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain E is discontinuous at line 8117.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 6935.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 6967.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 6999.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 7031.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 17506.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBu

In [13]:
pdbinfo_dict

{'1ERR.pdb': {<function id(obj, /)>: '1ERR.pdb',
  'coords': matrix([[53.995, 62.069, 72.653],
          [50.596, 62.259, 70.953],
          [51.799, 65.546, 69.479],
          [54.212, 64.025, 66.973],
          [53.347, 64.005, 63.307],
          [53.629, 60.694, 61.475],
          [57.   , 61.809, 60.232],
          [58.238, 63.006, 63.637],
          [57.248, 59.628, 65.129],
          [59.184, 57.774, 62.491],
          [62.423, 59.721, 62.777],
          [62.259, 59.753, 66.577],
          [61.958, 55.967, 66.457],
          [64.721, 55.511, 63.886],
          [67.033, 57.589, 66.105],
          [66.295, 55.442, 69.123],
          [67.392, 52.34 , 67.287],
          [69.755, 50.328, 69.431],
          [73.174, 49.603, 67.97 ],
          [73.891, 46.094, 66.592],
          [76.223, 44.386, 69.099],
          [78.752, 41.596, 68.506],
          [79.214, 38.169, 70.008],
          [82.025, 37.611, 72.521],
          [84.918, 37.609, 70.032],
          [85.796, 34.214, 68.578],
     

In [9]:
lfc_cutoff = 0.42
model = 'weighted-rig'

In [14]:
gsp_features = pd.DataFrame(columns=signals_wavelet+['class'])

In [15]:
gsp_features

Empty DataFrame
Columns: [molecular_weight_1, molecular_weight_2, molecular_weight_3, molecular_weight_4, hydrophobicity_1, hydrophobicity_2, hydrophobicity_3, hydrophobicity_4, node_degree_1, node_degree_2, node_degree_3, node_degree_4, node_weighted_degree_1, node_weighted_degree_2, node_weighted_degree_3, node_weighted_degree_4, residue_count_1, residue_count_2, residue_count_3, residue_count_4, clustering_coeff_1, clustering_coeff_2, clustering_coeff_3, clustering_coeff_4, conservation_score_1, conservation_score_2, conservation_score_3, conservation_score_4, class]
Index: []

[0 rows x 29 columns]

In [27]:
path_files = './pdb_files/ant_real/'
for pdb in pdbinfo_dict.keys():
    row = []
    c=0
    G = get_graph(pdbinfo_dict[pdb]['distance_matrix'], network_type=model, rig_cutoff=7.3)
    for signal_name in signals:
        signal = get_signal(G, pdbinfo_dict[pdb]['sequence'],pdb,signal=signal_name)
        value = get_filtered_signal(G,signal,lfc_cutoff,type_spatial='wavelet')       
        row.extend(value)
    row.append(c)
    gsp_features.loc[pdb] = row 

In [37]:
import pickle
with open('./files2/ago_dic.pkl', 'rb') as f:
    pdbinfo_dict_1 = pickle.load(f)

In [38]:
pdbinfo_dict_1

{'1EBP.pdb': {<function id(obj, /)>: '1EBP.pdb',
  'coords': matrix([[39.634, 30.133, 20.962],
          [36.868, 32.588, 22.026],
          [38.905, 34.036, 24.886],
          [41.903, 34.094, 22.571],
          [40.117, 35.912, 19.675],
          [38.375, 38.188, 22.194],
          [41.792, 38.796, 23.615],
          [43.007, 39.467, 20.042],
          [40.434, 42.21 , 19.443],
          [40.925, 43.941, 22.789],
          [42.247, 47.513, 23.274],
          [45.789, 48.669, 24.078],
          [47.739, 51.242, 26.045],
          [51.271, 52.542, 25.119],
          [54.731, 51.   , 25.689],
          [55.358, 49.952, 29.291],
          [58.147, 48.034, 31.001],
          [56.613, 44.996, 32.719],
          [58.208, 43.027, 35.554],
          [56.817, 40.403, 37.943],
          [58.021, 37.694, 40.463],
          [56.378, 34.219, 40.786],
          [58.006, 32.39 , 43.67 ],
          [60.084, 34.736, 45.716],
          [63.539, 34.21 , 44.144],
          [62.981, 35.244, 40.483],
     

In [39]:
model = 'weighted-rig'
# print (lfc_cutoff, end=' : ')
gsp_features_1 = pd.DataFrame(columns=signals_wavelet+['class'])

for pdb in pdbinfo_dict_1.keys():
#         print (pdb, end=', ')
    row = []
    c=1
    G = get_graph(pdbinfo_dict_1[pdb]['distance_matrix'], network_type=model, rig_cutoff=7.3)
    for signal_name, lfc_cutoff in signals_and_cutoffs.items():
        signal = get_signal(G, pdbinfo_dict_1[pdb]['sequence'],pdb, signal=signal_name)
        value = get_filtered_signal(G,signal,lfc_cutoff,type_spatial='wavelet')       
        row.extend(value)        
    row.append(c)
    gsp_features_1.loc[pdb] = row

/home/cellsearch/py_36_env/lib/python3.6/site-packages/pygsp/graphs/graph.py:496: RuntimeWarning: divide by zero encountered in power
  d = np.power(self.dw, -0.5)


In [40]:
gsp_f = pd.concat([gsp_features,gsp_features_1],axis=0)

X = gsp_f[gsp_f.columns.difference(['class'])]
y = gsp_f['class']

In [41]:
signal.shape

(253,)

In [35]:
len(pdbinfo_dict.keys())

156

In [42]:
gsp_features_1

molecular_weight_1  molecular_weight_2  molecular_weight_3  \
1EBP.pdb           70.779496           26.425562            0.276106   
1FCX.pdb           72.041204           24.616886            0.257090   
1FCY.pdb           71.774507           24.813398            0.259079   
1FCZ.pdb           71.641333           24.768340            0.259057   
1FM6.pdb           71.937346           27.862871            0.222513   
...                      ...                 ...                 ...   
6VIF.pdb           74.640365           26.523389            0.201263   
6W9H.pdb           73.912375           27.576416            0.251568   
6W9I.pdb           73.984356           27.752762            0.242819   
6WWZ.pdb           68.924962           18.995717            0.177328   
6XAE.pdb           73.965700           27.934338            0.243753   

          molecular_weight_4  hydrophobicity_1  hydrophobicity_2  \
1EBP.pdb            0.000654          0.184844          1.121956   
1FCX.pdb            0.000547          0.236775          1.176618   
1FCY.pdb            0.000549          0.280846          1.163933   
1FCZ.pdb            0.000551          0.261065          1.155173   
1FM6.pdb            0.000480          0.233965          1.234521   
...                      ...               ...               ...   
6VIF.pdb            0.000428          0.329931          1.266909   
6W9H.pdb            0.000497          0.373730          1.213114   
6W9I.pdb            0.000480          0.342279          1.227426   
6WWZ.pdb            0.000262          0.338022          1.234982   
6XAE.pdb            0.000482          0.339903          1.204985   

          hydrophobicity_3  hydrophobicity_4  node_degree_1  node_degree_2  \
1EBP.pdb          0.019290          0.000046       4.954575       0.861792   
1FCX.pdb          0.018181          0.000039       4.916267       1.067916   
1FCY.pdb          0.017831          0.000038       4.920244       1.021809   
1FCZ.pdb          0.018150          0.000039       4.920575       1.054250   
1FM6.pdb          0.016605          0.000036       5.062072       1.139770   
...                    ...               ...            ...            ...   
6VIF.pdb          0.019409          0.000041       4.847094       0.997561   
6W9H.pdb          0.018944          0.000037       4.982009       1.111867   
6W9I.pdb          0.018661          0.000037       4.980641       1.120368   
6WWZ.pdb          0.010228          0.000015       4.987110       0.841872   
6XAE.pdb          0.019405          0.000038       4.962553       1.146851   

          ...  residue_count_4  clustering_coeff_1  clustering_coeff_2  \
1EBP.pdb  ...         0.000118            0.280298            0.150925   
1FCX.pdb  ...         0.000153            0.282164            0.138746   
1FCY.pdb  ...         0.000150            0.284078            0.135504   
1FCZ.pdb  ...         0.000156            0.281990            0.132787   
1FM6.pdb  ...         0.000110            0.288484            0.158782   
...       ...              ...                 ...                 ...   
6VIF.pdb  ...         0.000157            0.306519            0.143404   
6W9H.pdb  ...         0.000128            0.285111            0.158221   
6W9I.pdb  ...         0.000128            0.285014            0.153838   
6WWZ.pdb  ...         0.000058            0.268356            0.094176   
6XAE.pdb  ...         0.000133            0.287059            0.155573   

          clustering_coeff_3  clustering_coeff_4  conservation_score_1  \
1EBP.pdb            0.001208            0.000003              0.453421   
1FCX.pdb            0.001133            0.000002              0.465685   
1FCY.pdb            0.001128            0.000002              0.465173   
1FCZ.pdb            0.001143            0.000002              0.464861   
1FM6.pdb            0.001003            0.000002              0.469322   
...                      ...                 ...          

In [43]:
gsp_features

molecular_weight_1  molecular_weight_2  molecular_weight_3  \
1ERR.pdb           64.113203           13.390872            0.167218   
1FTL.pdb           70.173009           24.311121            0.222586   
1LK2.pdb           73.642242           27.046798            0.214666   
1NHZ.pdb           74.245257           24.223986            0.210313   
1PBQ.pdb           70.463795           23.890169            0.217301   
...                      ...                 ...                 ...   
6UZA.pdb           72.055373           24.290123            0.075449   
6V4P.pdb           68.387123           24.385745            0.123315   
6V9S.pdb           73.307653           23.366619            0.111742   
6W25.pdb           70.903560           23.476416            0.122271   
6ZHO.pdb           69.695990           26.461196            0.106890   

          molecular_weight_4  hydrophobicity_1  hydrophobicity_2  \
1ERR.pdb            0.000372          0.293257          1.357203   
1FTL.pdb            0.000433          0.401456          1.194749   
1LK2.pdb            0.000392          0.265787          1.218032   
1NHZ.pdb            0.000440          0.249947          1.223520   
1PBQ.pdb            0.000397          0.261474          1.227107   
...                      ...               ...               ...   
6UZA.pdb            0.000051          0.495355          1.246897   
6V4P.pdb            0.000136          0.179745          1.132644   
6V9S.pdb            0.000111          0.450447          1.148140   
6W25.pdb            0.000131          0.623548          1.191057   
6ZHO.pdb            0.000093          0.225116          1.191795   

          hydrophobicity_3  hydrophobicity_4  node_degree_1  node_degree_2  \
1ERR.pdb          0.015656          0.000035       3.510459       0.127208   
1FTL.pdb          0.014850          0.000029       5.181291       1.162616   
1LK2.pdb          0.013091          0.000024       5.061551       1.005204   
1NHZ.pdb          0.017202          0.000036       4.778333       0.880368   
1PBQ.pdb          0.013249          0.000024       5.112982       1.085919   
...                    ...               ...            ...            ...   
6UZA.pdb          0.005413          0.000004       4.775746       0.942011   
6V4P.pdb          0.007578          0.000008       5.924166       1.008877   
6V9S.pdb          0.008392          0.000008       5.093060       1.016212   
6W25.pdb          0.008661          0.000009       5.311700       1.112669   
6ZHO.pdb          0.006336          0.000005       5.247781       1.240078   

          ...  residue_count_4  clustering_coeff_1  clustering_coeff_2  \
1ERR.pdb  ...         0.000163            0.318637            0.087923   
1FTL.pdb  ...         0.000073            0.277791            0.136593   
1LK2.pdb  ...         0.000065            0.282789            0.145858   
1NHZ.pdb  ...         0.000121            0.308139            0.127541   
1PBQ.pdb  ...         0.000050            0.273369            0.132528   
...       ...              ...                 ...                 ...   
6UZA.pdb  ...         0.000026            0.292523            0.128112   
6V4P.pdb  ...         0.000050            0.259472            0.123318   
6V9S.pdb  ...         0.000043            0.287075            0.126058   
6W25.pdb  ...         0.000053            0.277043            0.124538   
6ZHO.pdb  ...         0.000030            0.269288            0.137448   

          clustering_coeff_3  clustering_coeff_4  conservation_score_1  \
1ERR.pdb            0.001029        2.287257e-06              0.406765   
1FTL.pdb            0.001198        2.330290e-06              0.456963   
1LK2.pdb            0.000939        1.712731e-06              0.469035   
1NHZ.pdb            0.001125        2.353066e-06              0.469533   
1PBQ.pdb            0.001039        1.895173e-06              0.451293   
...                      ...                 ...          

In [44]:
gsp_f

molecular_weight_1  molecular_weight_2  molecular_weight_3  \
1ERR.pdb           64.113203           13.390872            0.167218   
1FTL.pdb           70.173009           24.311121            0.222586   
1LK2.pdb           73.642242           27.046798            0.214666   
1NHZ.pdb           74.245257           24.223986            0.210313   
1PBQ.pdb           70.463795           23.890169            0.217301   
...                      ...                 ...                 ...   
6VIF.pdb           74.640365           26.523389            0.201263   
6W9H.pdb           73.912375           27.576416            0.251568   
6W9I.pdb           73.984356           27.752762            0.242819   
6WWZ.pdb           68.924962           18.995717            0.177328   
6XAE.pdb           73.965700           27.934338            0.243753   

          molecular_weight_4  hydrophobicity_1  hydrophobicity_2  \
1ERR.pdb            0.000372          0.293257          1.357203   
1FTL.pdb            0.000433          0.401456          1.194749   
1LK2.pdb            0.000392          0.265787          1.218032   
1NHZ.pdb            0.000440          0.249947          1.223520   
1PBQ.pdb            0.000397          0.261474          1.227107   
...                      ...               ...               ...   
6VIF.pdb            0.000428          0.329931          1.266909   
6W9H.pdb            0.000497          0.373730          1.213114   
6W9I.pdb            0.000480          0.342279          1.227426   
6WWZ.pdb            0.000262          0.338022          1.234982   
6XAE.pdb            0.000482          0.339903          1.204985   

          hydrophobicity_3  hydrophobicity_4  node_degree_1  node_degree_2  \
1ERR.pdb          0.015656          0.000035       3.510459       0.127208   
1FTL.pdb          0.014850          0.000029       5.181291       1.162616   
1LK2.pdb          0.013091          0.000024       5.061551       1.005204   
1NHZ.pdb          0.017202          0.000036       4.778333       0.880368   
1PBQ.pdb          0.013249          0.000024       5.112982       1.085919   
...                    ...               ...            ...            ...   
6VIF.pdb          0.019409          0.000041       4.847094       0.997561   
6W9H.pdb          0.018944          0.000037       4.982009       1.111867   
6W9I.pdb          0.018661          0.000037       4.980641       1.120368   
6WWZ.pdb          0.010228          0.000015       4.987110       0.841872   
6XAE.pdb          0.019405          0.000038       4.962553       1.146851   

          ...  residue_count_4  clustering_coeff_1  clustering_coeff_2  \
1ERR.pdb  ...         0.000163            0.318637            0.087923   
1FTL.pdb  ...         0.000073            0.277791            0.136593   
1LK2.pdb  ...         0.000065            0.282789            0.145858   
1NHZ.pdb  ...         0.000121            0.308139            0.127541   
1PBQ.pdb  ...         0.000050            0.273369            0.132528   
...       ...              ...                 ...                 ...   
6VIF.pdb  ...         0.000157            0.306519            0.143404   
6W9H.pdb  ...         0.000128            0.285111            0.158221   
6W9I.pdb  ...         0.000128            0.285014            0.153838   
6WWZ.pdb  ...         0.000058            0.268356            0.094176   
6XAE.pdb  ...         0.000133            0.287059            0.155573   

          clustering_coeff_3  clustering_coeff_4  conservation_score_1  \
1ERR.pdb            0.001029            0.000002              0.406765   
1FTL.pdb            0.001198            0.000002              0.456963   
1LK2.pdb            0.000939            0.000002              0.469035   
1NHZ.pdb            0.001125            0.000002              0.469533   
1PBQ.pdb            0.001039            0.000002              0.451293   
...                      ...                 ...          

In [45]:
from sklearn import svm
from sklearn.model_selection import train_test_split
from sklearn import metrics

#Create a svm Classifier
clf = svm.SVC(kernel='rbf') # Linear Kernel

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3,random_state=109)

#Train the model using the training sets
clf.fit(X_train, y_train)

#Predict the response for test dataset
y_pred = clf.predict(X_test)

# Model Accuracy: how often is the classifier correct?
print("Accuracy:",metrics.accuracy_score(y_test, y_pred))

# Model Precision: what percentage of positive tuples are labeled as such?
print("Precision:",metrics.precision_score(y_test, y_pred))

# Model Recall: what percentage of positive tuples are labelled as such?
print("Recall:",metrics.recall_score(y_test, y_pred))

from sklearn.metrics import classification_report, confusion_matrix 
print(classification_report(y_test, y_pred)) 

Accuracy: 0.7108433734939759
Precision: 0.7108433734939759
Recall: 1.0
              precision    recall  f1-score   support

         0.0       0.00      0.00      0.00        48
         1.0       0.71      1.00      0.83       118

    accuracy                           0.71       166
   macro avg       0.36      0.50      0.42       166
weighted avg       0.51      0.71      0.59       166



/home/cellsearch/py_36_env/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/cellsearch/py_36_env/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/cellsearch/py_36_env/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [46]:
gsp_f

molecular_weight_1  molecular_weight_2  molecular_weight_3  \
1ERR.pdb           64.113203           13.390872            0.167218   
1FTL.pdb           70.173009           24.311121            0.222586   
1LK2.pdb           73.642242           27.046798            0.214666   
1NHZ.pdb           74.245257           24.223986            0.210313   
1PBQ.pdb           70.463795           23.890169            0.217301   
...                      ...                 ...                 ...   
6VIF.pdb           74.640365           26.523389            0.201263   
6W9H.pdb           73.912375           27.576416            0.251568   
6W9I.pdb           73.984356           27.752762            0.242819   
6WWZ.pdb           68.924962           18.995717            0.177328   
6XAE.pdb           73.965700           27.934338            0.243753   

          molecular_weight_4  hydrophobicity_1  hydrophobicity_2  \
1ERR.pdb            0.000372          0.293257          1.357203   
1FTL.pdb            0.000433          0.401456          1.194749   
1LK2.pdb            0.000392          0.265787          1.218032   
1NHZ.pdb            0.000440          0.249947          1.223520   
1PBQ.pdb            0.000397          0.261474          1.227107   
...                      ...               ...               ...   
6VIF.pdb            0.000428          0.329931          1.266909   
6W9H.pdb            0.000497          0.373730          1.213114   
6W9I.pdb            0.000480          0.342279          1.227426   
6WWZ.pdb            0.000262          0.338022          1.234982   
6XAE.pdb            0.000482          0.339903          1.204985   

          hydrophobicity_3  hydrophobicity_4  node_degree_1  node_degree_2  \
1ERR.pdb          0.015656          0.000035       3.510459       0.127208   
1FTL.pdb          0.014850          0.000029       5.181291       1.162616   
1LK2.pdb          0.013091          0.000024       5.061551       1.005204   
1NHZ.pdb          0.017202          0.000036       4.778333       0.880368   
1PBQ.pdb          0.013249          0.000024       5.112982       1.085919   
...                    ...               ...            ...            ...   
6VIF.pdb          0.019409          0.000041       4.847094       0.997561   
6W9H.pdb          0.018944          0.000037       4.982009       1.111867   
6W9I.pdb          0.018661          0.000037       4.980641       1.120368   
6WWZ.pdb          0.010228          0.000015       4.987110       0.841872   
6XAE.pdb          0.019405          0.000038       4.962553       1.146851   

          ...  residue_count_4  clustering_coeff_1  clustering_coeff_2  \
1ERR.pdb  ...         0.000163            0.318637            0.087923   
1FTL.pdb  ...         0.000073            0.277791            0.136593   
1LK2.pdb  ...         0.000065            0.282789            0.145858   
1NHZ.pdb  ...         0.000121            0.308139            0.127541   
1PBQ.pdb  ...         0.000050            0.273369            0.132528   
...       ...              ...                 ...                 ...   
6VIF.pdb  ...         0.000157            0.306519            0.143404   
6W9H.pdb  ...         0.000128            0.285111            0.158221   
6W9I.pdb  ...         0.000128            0.285014            0.153838   
6WWZ.pdb  ...         0.000058            0.268356            0.094176   
6XAE.pdb  ...         0.000133            0.287059            0.155573   

          clustering_coeff_3  clustering_coeff_4  conservation_score_1  \
1ERR.pdb            0.001029            0.000002              0.406765   
1FTL.pdb            0.001198            0.000002              0.456963   
1LK2.pdb            0.000939            0.000002              0.469035   
1NHZ.pdb            0.001125            0.000002              0.469533   
1PBQ.pdb            0.001039            0.000002              0.451293   
...                      ...                 ...          

In [47]:
path = './pdb_files/ant_real/'
pdbinfo_dict = crawl_pdb(path)
lfc_cutoff = 0.42
model = 'weighted-rig'
# print (lfc_cutoff, end=' : ')
gsp_features = pd.DataFrame(columns=signals_wavelet+['class'])
 
path_files = './pdb_files/ant_real/'
for pdb in pdbinfo_dict.keys():
    row = []
    c=0
    G = get_graph(pdbinfo_dict[pdb]['distance_matrix'], network_type=model, rig_cutoff=7.3)
    for signal_name in signals:
        signal = get_signal(G, pdbinfo_dict[pdb]['sequence'],pdb,signal=signal_name)
        value = get_filtered_signal(G,signal,lfc_cutoff,type_spatial='wavelet')       
        row.extend(value)
    row.append(c)
    gsp_features.loc[pdb] = row
    break

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4092.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4126.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4160.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4211.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4344.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4930.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4977.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 5024.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 5231.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4641.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 13462.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 13487.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 13512.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 13537.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain E is discontinuous at line 13562.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/Structu

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4503.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 4522.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4539.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 4775.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 8804.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 12529.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 25061.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 25088.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 25115.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 25142.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/Structu

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4082.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4167.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4251.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4365.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 3445.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4898.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4903.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4942.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 5125.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4916.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 7888.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 7946.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 8003.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 8060.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain E is discontinuous at line 8117.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 8070.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 2615.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 6935.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 6967.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBuilder.py:92: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 6999.
  PDBConstructionWarning,
/home/cellsearch/py_36_env/lib/python3.6/site-packages/Bio/PDB/StructureBui

In [48]:
pdb

'1ERR.pdb'

In [49]:
pdbinfo_dict

{'1ERR.pdb': {<function id(obj, /)>: '1ERR.pdb',
  'coords': matrix([[53.995, 62.069, 72.653],
          [50.596, 62.259, 70.953],
          [51.799, 65.546, 69.479],
          [54.212, 64.025, 66.973],
          [53.347, 64.005, 63.307],
          [53.629, 60.694, 61.475],
          [57.   , 61.809, 60.232],
          [58.238, 63.006, 63.637],
          [57.248, 59.628, 65.129],
          [59.184, 57.774, 62.491],
          [62.423, 59.721, 62.777],
          [62.259, 59.753, 66.577],
          [61.958, 55.967, 66.457],
          [64.721, 55.511, 63.886],
          [67.033, 57.589, 66.105],
          [66.295, 55.442, 69.123],
          [67.392, 52.34 , 67.287],
          [69.755, 50.328, 69.431],
          [73.174, 49.603, 67.97 ],
          [73.891, 46.094, 66.592],
          [76.223, 44.386, 69.099],
          [78.752, 41.596, 68.506],
          [79.214, 38.169, 70.008],
          [82.025, 37.611, 72.521],
          [84.918, 37.609, 70.032],
          [85.796, 34.214, 68.578],
     

In [50]:
gsp_features

molecular_weight_1  molecular_weight_2  molecular_weight_3  \
1ERR.pdb            73.70339           22.779563            0.233207   

          molecular_weight_4  hydrophobicity_1  hydrophobicity_2  \
1ERR.pdb            0.000518          0.449012           1.19651   

          hydrophobicity_3  hydrophobicity_4  node_degree_1  node_degree_2  \
1ERR.pdb          0.018989          0.000042       4.974301       0.923667   

          ...  residue_count_4  clustering_coeff_1  clustering_coeff_2  \
1ERR.pdb  ...         0.000185            0.296468            0.129666   

          clustering_coeff_3  clustering_coeff_4  conservation_score_1  \
1ERR.pdb            0.001172            0.000003              0.471706   

          conservation_score_2  conservation_score_3  conservation_score_4  \
1ERR.pdb              0.134558              0.001035              0.000002   

          class  
1ERR.pdb    0.0  

[1 rows x 29 columns]